# TO DO
- Add functionality to model generator for non-composite deck
- add functionality for beam offsets? (included in transformation)
- reaction arrows in model plot? ('cone' objects can't be toggled on/off)
- show load vector
- Put in a 'dummy' trace in the girder results so theres only 1 color bar 
- move results data into pandas dataframes (if needed)
- Compute composite moment (this is quite a bit of code, not sure it belongs here)
- Compare to strand7 (check analysis, confirm beam orientations etc.)
- get better at markdown

# Make a model & Run it with OpenSEES

This code accepts user input of a simple span multi-girder bridge parameters, then builds and analyzes a static model using the OpenSEES software through the python module OpenSeesPy.

Model plots are generated in Plotly.

The first few cells are functions used to build and analyze the model, jump to user input here: [User Inputs](#inputcell)

In [35]:
# Imports
import sys
#sys.path.append(r'C:\Users\tgolecki\AppData\Local\Continuum\anaconda3\Lib\site-packages\openseespy')
#import opensees
import openseespy.opensees as opensees
import math
import copy
import pprint
import functools
import numpy as np
import plotly.offline as py
import plotly.graph_objs as go
py.init_notebook_mode(connected=True)
pp = pprint.PrettyPrinter(indent=4)

# Generate Model
This command accepts the user input parameters and defines the mesh, element and link connectivity. X direction is longitudinal, Y direction is transverse and Z is vertical. The mesh is rectangular with no checks for rounding or aspect ratio, so the inputs need to be considerate of other geometry that could result in very closely spaced nodes.

The mesh is determined by first locating the 'hard points' that must be included in the mesh. These are the start and end locations of girder properties and deck regions and locations of diaphragms. Once these hard points are determined, the space between them is meshed using a maximim element size according to the user input. 

There are 3 planes of nodes, the deck elevation, the girder elevation, and the boundary condition elevation. Nodes on the deck plane are in the 1,000,000s. Nodes in the girder plate are in the 2,000,000s. Nodes in the boundary conditon plane are in the 3,000,000s. In the y direction, gridlines use the hundred thousands places, in the x direction gridlines use the hundreds places. So node 1,002,003 is in the deck plane (1,000,000) on the second grid line in the y direction (0,002,000) and the third grid line in the x direction (0,000,003). In this way node coordinates are coded into the node number, making connectivity possible by incrementing node numbers. 

Girder element numbers are set as the i node number, link 'element' numbers are set as the j node number (because master nodes 'i' may be re-used where slave nodes 'j' may not) Diaphragm beam elements require an offset to avoid duplicating element numbers with girders. 

In [36]:
def GenerateModel(Model_Inp):
    """"
    Function to generate model components (NODES, SHELLS, BEAMS LINKS, BCS)

    """
    Mesh_X = Model_Inp['Mesh_X']
    Mesh_Y = Model_Inp['Mesh_Y']
    Deck_inp = Model_Inp['Deck_inp']
    Girders_inp = Model_Inp['Girders_inp']
    Diaphragms_inp = Model_Inp['Diaphragms_inp']
    BC_inp = Model_Inp['BC_inp']
    Comp_inp = Model_Inp['Comp_inp']

    # find the hard points that must contain a mesh line, then mesh between them according to the mesh size input
    girderpoints_x = list(set(
        [y for x in [Girders_inp[x][::2] for x in Girders_inp] for y in x]))
    deckpoints_x = list(set(
        [y for x in [[Deck_inp[x][0][0], Deck_inp[x][0][1]] for x in Deck_inp] for y in x]))
    diaphragmpoints_x = sorted(Diaphragms_inp.keys())
    
    girderpoints_y = sorted(Girders_inp.keys())
    deckpoints_y = list(set(
        [y for x in [[Deck_inp[x][1][0], Deck_inp[x][1][1]] for x in Deck_inp] for y in x]))
    
    gx = sorted(list(set(deckpoints_x + diaphragmpoints_x + girderpoints_x)))
    gy = sorted(list(set(girderpoints_y + deckpoints_y)))

    # find the number of divisions between hard points
    ptsbetweenx = [math.ceil((gx[i+1]-gx[i])/Mesh_X) for i in range(len(gx)-1)]
    ptsbetweeny = [math.ceil((gy[i+1]-gy[i])/Mesh_Y) for i in range(len(gy)-1)]

    # make the mesh lines between the hard points (and including the hard points)
    gridx = copy.deepcopy(gx)
    for i, px in enumerate(ptsbetweenx):
        dx = (gx[i+1]-gx[i])/px
        for ii in range(px):
            x = dx*ii + gx[i]
            gridx.append(x)
    gridx = sorted(set(gridx))

    gridy = copy.deepcopy(gy)
    for i, py in enumerate(ptsbetweeny):
        dy = (gy[i+1]-gy[i])/py
        for ii in range(py):
            y = dy*ii + gy[i]
            gridy.append(y)
    gridy = sorted(set(gridy))

    #print("Mesh is "+str(len(gridx))+" by "+str(len(gridy)) + " nodes")

    # mesh the grid
    # node numbering for grid, 1e6 + 1000*yindex + xindex

    # initialize output dictionaries
    NODES = {}
    # NODES[n]=[x,y,z]
    BEAMS = {}
    # BEAMS[el]=[n1,n2,mat,prop]
    SHELLS = {}
    #SHELLS[el] = {'nodes':[n1,n2,n3,n4],'prop':no}
    LINKS = {}
    # LINKS[l]=[n1,n2...]
    BCS = {}
    #BCS[n] = [dof1,dof2,dof3,dof4,dof5,dof6]

    # Make nodes on deck
    for j, y in enumerate(gridy):
        for i, x in enumerate(gridx):
            # start with index 1 for node numbering to avoid a node number 0
            NODES[1000000+1000 *
                  (j+1)+(i+1)] = {'x': float(x), 'y': float(y), 'z': float(0)}

    # make the deck shells
    SHELLS = {}
    for d in Deck_inp:
        for j, y in enumerate(gridy[:-1]):
            for i, x in enumerate(gridx[:-1]):
                #print(Deck_inp[d][1][0] , y)
                if all([Deck_inp[d][1][0] <= y, y <= Deck_inp[d][1][1], Deck_inp[d][0][0] <= x, x <= Deck_inp[d][0][1]]):
                    # shell element numbers use the n1 node, (-x,-y node)
                    n1 = 1000000+1000*(j+1)+(i+1)
                    n2 = n1+1
                    n3 = n2+1000
                    n4 = n1+1000
                    SHELLS[n1] = {'nodes': [n1, n2, n3, n4], 'prop': Deck_inp[d][2]}

    # Make nodes on girders and girder elements, 2e6 + 1000*yindex + xindex
    for y in sorted(Girders_inp.keys()):
        gx = Girders_inp[y][::2]
        j = gridy.index(y)
        for i, x in enumerate(gridx):
            # 2,000,000s for girder nodes
            n = 2000000+1000*(j+1)+(i+1)
            NODES[n] = {'x': float(x), 'y': float(y), 'z': float(Girders_inp[y][-1])}
            if x < gridx[-1]:
                for g in range(len(gx)-1):
                    if gx[g] <= x and x < gx[g+1]:
                        prop = Girders_inp[y][2*g+1]
                BEAMS[n] = [n, n+1, prop]

    # Make diaphragm elements (4e6)
    for x in sorted(Diaphragms_inp.keys()):
        i = gridx.index(x)
        gy = sorted(Girders_inp.keys())
        for gj in range(len(gy)-1):
            j1 = gridy.index(gy[gj])
            j2 = gridy.index(gy[gj+1])
            n1 = 2000000+1000*(j1+1)+(i+1)
            n2 = 2000000+1000*(j2+1)+(i+1)
            BEAMS[4000000+1000*(j1+1)+(i+1)] = [n1, n2, Diaphragms_inp[x]]

    # Make nodes on BC, 3e6 + 1000*yindex + xindex
    linked = []
    for coord in sorted(BC_inp.keys()):
        # x and y should already be in gridx, gridy
        x = coord[0]
        y = coord[1]
        z = coord[2]
        i = gridx.index(x)
        j = gridy.index(y)
        n = 3000000+1000*(j+1)+(i+1)
        NODES[n] = {'x': float(x), 'y': float(y), 'z': float(z)}
        BCS[n] = BC_inp[coord]
        # LINKS[n-1000000]=[n,n-1000000]
        # LINKS[n-2000000]=[n,n-2000000]
        # use stiff beams instead of links to enable extracting reactions
        BEAMS[5000000+1000*(j+1)+(i+1)] = [n, n-1000000, 5]
        # linked.append(n-1000000)

    # Make Girder to deck links
    for y in sorted(Girders_inp.keys()):
        gx = Girders_inp[y][::2]
        j = gridy.index(y)
        for i, x in enumerate(gridx):
            # 2,000,000s for girder nodes
            n = 2000000+1000*(j+1)+(i+1)
            if n not in linked:
                LINKS[n-1000000] = [n, n-1000000,Comp_inp]
    MODEL = {'NODES': NODES, 'SHELLS': SHELLS, 'BEAMS': BEAMS, 'LINKS': LINKS, 'BCS': BCS}
    MODEL.update(Model_Inp)
    return MODEL,gridx,gridy

# PlotModel
The plot model function accepts the model definition and returns a 3d scatter and mesh plot in plotly. Currently the mesh plot (of shell elements) cannot be toggled off. The DISP and dispfactor inputs are optional, if provided the model will be rendered in its deformed shape scaled by the dispfactor. 

In [37]:
def PlotModel(MODEL, includeshells=True, RESULTS={}, dispfactor=0, dof='ALL'):
    """"
    Function to generate model plot in plotly

    """
    NODES = MODEL['NODES']
    SHELLS = MODEL['SHELLS']
    BEAMS = MODEL['BEAMS']
    LINKS = MODEL['LINKS']
    BCS = MODEL['BCS']

    if RESULTS == {}:
        DISP = {}
        for n in sorted(NODES.keys()):
            DISP[n] = {'x': 0, 'y': 0, 'z': 0}
        REACTIONS = {}
        dispfactor = 0
        dof = 'ALL'
    else:
        DISP = RESULTS['DISP']
        REACTIONS = RESULTS['REACTIONS']

    # shells (as a mesh)
    shell_trace = []
    faces = []
    shellnodes = {}
    counter = 0
    x = []
    y = []
    z = []
    if includeshells:
        for s in sorted(SHELLS.keys()):
            for n in SHELLS[s]['nodes']:
                x.append(NODES[n]['x'] + dispfactor*DISP[n]['x'])
                y.append(NODES[n]['y'] + dispfactor*DISP[n]['y'])
                z.append(NODES[n]['z'] + dispfactor*DISP[n]['z'])
                shellnodes[n] = counter
                counter += 1
        faces = []
        for s in sorted(SHELLS.keys()):
            faces.append(np.asarray([shellnodes[SHELLS[s]['nodes'][0]],
                                     shellnodes[SHELLS[s]['nodes'][1]],
                                     shellnodes[SHELLS[s]['nodes'][2]]]))
            faces.append(np.asarray([shellnodes[SHELLS[s]['nodes'][2]],
                                     shellnodes[SHELLS[s]['nodes'][3]],
                                     shellnodes[SHELLS[s]['nodes'][0]]]))

        points3D = np.vstack((x, y, z)).T
        tri_vertices = list(map(lambda index: points3D[index], faces))
        I, J, K = ([triplet[c] for triplet in faces] for c in range(3))
        shell_trace = dict(type='mesh3d', lighting=dict(fresnel=0.2, roughness=0.5, specular=0.05, ambient=0.8, diffuse=0.8),
                           flatshading=True, opacity=0.25, x=x, y=y, z=z, color='green', i=I, j=J, k=K, name='Shells',
                           legendgroup='shells')

        lists_coord = [[[T[k][c] for k in range(3)]+[None] for T in tri_vertices] for c in range(3)]
        Xe, Ye, Ze = [functools.reduce(lambda x, y: x+y, lists_coord[k]) for k in range(3)]
        shelledge_trace = dict(type='scatter3d', legendgroup='shells', showlegend=False, x=Xe, y=Ye, z=Ze,
                               mode='lines', line=dict(color='rgb(150,150,150)', width=1.0), hoverinfo='none')

    # nodes
    x = [NODES[n]['x'] + dispfactor*DISP[n]['x'] for n in sorted(NODES.keys())]
    y = [NODES[n]['y'] + dispfactor*DISP[n]['y'] for n in sorted(NODES.keys())]
    z = [NODES[n]['z'] + dispfactor*DISP[n]['z'] for n in sorted(NODES.keys())]
    n = sorted(NODES.keys())

    if dispfactor == 0:
        node_trace = go.Scatter3d(x=x, y=y, z=z, mode='markers', marker=dict(
            size=1, color='blue'), name='Nodes', text=n)
    else:
        dof = dof.lower()
        if dof == 'all':
            mxd = max([(DISP[n]['x']**2 + DISP[n]['y']**2 + DISP[n]
                        ['z']**2)**0.5 for n in sorted(NODES.keys())])
            mnd = min([(DISP[n]['x']**2 + DISP[n]['y']**2 + DISP[n]
                        ['z']**2)**0.5 for n in sorted(NODES.keys())])
            nodecolor = [(DISP[n]['x']**2 + DISP[n]['y']**2 +
                          DISP[n]['z']**2)**0.5 for n in sorted(NODES.keys())]
        else:
            mxd = max([DISP[n][dof] for n in sorted(NODES.keys())])
            mnd = min([DISP[n][dof] for n in sorted(NODES.keys())])
            nodecolor = [DISP[n][dof] for n in sorted(NODES.keys())]
        text = ["node:"+str(n)+"<br>dx:"+"%5f" % DISP[n]['x']+"<br>dy:"+"%5f" %
                DISP[n]['y']+"<br>dz:"+"%5f" % DISP[n]['z'] for n in sorted(NODES.keys())]
        node_trace = go.Scatter3d(x=x, y=y, z=z, text=text, mode='markers',
                                  marker=dict(size=2, color=nodecolor, colorscale='Viridis',
                                              colorbar=dict(title=dof.upper(), x=0, xanchor='right')),
                                  name='Nodes')

    # beams
    DEFAULT_PLOTLY_COLORS = ['rgb(31, 119, 180)', 'rgb(255, 127, 14)',
                             'rgb(44, 160, 44)', 'rgb(214, 39, 40)',
                             'rgb(148, 103, 189)', 'rgb(140, 86, 75)',
                             'rgb(227, 119, 194)', 'rgb(127, 127, 127)',
                             'rgb(188, 189, 34)', 'rgb(23, 190, 207)']

    beam_trace = []
    for b in sorted(BEAMS.keys()):
        if b == sorted(BEAMS.keys())[0]:
            showlegend = True
        else:
            showlegend = False
        beam_trace.append(go.Scatter3d(x=[NODES[BEAMS[b][0]]['x'] + dispfactor*DISP[BEAMS[b][0]]['x'],
                                           NODES[BEAMS[b][1]]['x'] + dispfactor*DISP[BEAMS[b][1]]['x']],
                                       y=[NODES[BEAMS[b][0]]['y'] + dispfactor*DISP[BEAMS[b][0]]['y'],
                                           NODES[BEAMS[b][1]]['y'] + dispfactor*DISP[BEAMS[b][1]]['y']],
                                       z=[NODES[BEAMS[b][0]]['z'] + dispfactor*DISP[BEAMS[b][0]]['z'],
                                           NODES[BEAMS[b][1]]['z'] + dispfactor*DISP[BEAMS[b][1]]['z']],
                                       mode='lines', legendgroup='beams', showlegend=showlegend, text=b,
                                       name='Beams', line=dict(color=DEFAULT_PLOTLY_COLORS[BEAMS[b][2]])))

    link_trace = []
    for l in sorted(LINKS.keys()):
        if l == sorted(LINKS.keys())[0]:
            showlegend = True
        else:
            showlegend = False
        link_trace.append(go.Scatter3d(x=[NODES[LINKS[l][0]]['x'] + dispfactor*DISP[LINKS[l][0]]['x'],
                                           NODES[LINKS[l][1]]['x'] + dispfactor*DISP[LINKS[l][1]]['x']],
                                       y=[NODES[LINKS[l][0]]['y'] + dispfactor*DISP[LINKS[l][0]]['y'],
                                           NODES[LINKS[l][1]]['y'] + dispfactor*DISP[LINKS[l][1]]['y']],
                                       z=[NODES[LINKS[l][0]]['z'] + dispfactor*DISP[LINKS[l][0]]['z'],
                                           NODES[LINKS[l][1]]['z'] + dispfactor*DISP[LINKS[l][1]]['z']],
                                       mode='lines', legendgroup='links', showlegend=showlegend, name='Links',
                                       text=l, line=dict(color='black')))

    # plot reactions as vectors & cones
    R_sf = 0.1
    bc_trace = []
    colorscaleblack = [[0, 'black'], [1.0, 'black']]

    for i in ['x', 'y', 'z']:
        showlegend = True
        for n in sorted(REACTIONS.keys()):
            x0 = NODES[n]['x'] + dispfactor*DISP[n]['x']
            y0 = NODES[n]['y'] + dispfactor*DISP[n]['y']
            z0 = NODES[n]['z'] + dispfactor*DISP[n]['z']

            if BCS[n][['x', 'y', 'z'].index(i)] == 1:
                if i == 'x':
                    x1, y1, z1 = x0-(R_sf*REACTIONS[n][0]), y0, z0
                elif i == 'y':
                    x1, y1, z1 = x0, y0-(R_sf*REACTIONS[n][1]), z0
                elif i == 'z':
                    x1, y1, z1 = x0, y0, z0-(R_sf*REACTIONS[n][2])

                bc_trace.append(go.Scatter3d(x=[x0, x1], y=[y0, y1], z=[z0, z1], hoverinfo='text', visible='legendonly',
                                             mode='lines', legendgroup=i, showlegend=showlegend,
                                             text=REACTIONS[n][['x', 'y', 'z'].index(i)],
                                             name='BC_'+i, line=dict(color='black', width=6)))
                if showlegend:
                    showlegend = False
                # if i=='x':
                #    bc_trace.append({'type': 'cone','x': [x0], 'y': [y0], 'z': [z0],'u': [math.copysign(20,REACTIONS[n][0])], 'v': [0], 'w': [0], 'showscale':False,'legendgroup':i,'anchor':'tip','colorscale':colorscaleblack,'showlegend':True,'hoverinfo':'text','text':REACTIONS[n][['x','y','z'].index(i)],'visible':True})
                # elif i=='y':
                #    bc_trace.append({'type': 'cone','x': [x0], 'y': [y0], 'z': [z0],'u': [0], 'v': [math.copysign(20,REACTIONS[n][1])], 'w': [0], 'showscale':False,'legendgroup':i,'anchor':'tip','colorscale':colorscaleblack,'showlegend':True,'hoverinfo':'text','text':REACTIONS[n][['x','y','z'].index(i)],'visible':True})
                # elif i=='z':
                #    bc_trace.append({'type': 'cone','x': [x0], 'y': [y0], 'z': [z0],'u': [0], 'v': [0], 'w': [math.copysign(20,REACTIONS[n][2])], 'showscale':False,'legendgroup':i,'anchor':'tip','colorscale':colorscaleblack,'showlegend':True,'hoverinfo':'text','text':REACTIONS[n][['x','y','z'].index(i)],'visible':True})

    # layout
    noaxis = dict(showbackground=False, showline=False, zeroline=False, showgrid=False, showticklabels=False, title='')
    layout = dict(title='Model', scene=dict(aspectmode='data', xaxis=noaxis, yaxis=noaxis, zaxis=noaxis))
    if includeshells:
        fig = go.Figure(data=[node_trace]+beam_trace+link_trace +
                        [shell_trace]+[shelledge_trace]+bc_trace, layout=layout)
    else:
        fig = go.Figure(data=[node_trace]+beam_trace+link_trace + bc_trace, layout=layout)
    py.iplot(fig)
    return None

# BuildOpenSEES
This function converts the generic nodal coordinates and connectivity into an OpenSEES model. There are assumptions in here for element type and beam orientation. 

Beam element orientation is described here
__[http://opensees.berkeley.edu/wiki/index.php/Linear_Transformation](http://opensees.berkeley.edu/wiki/index.php/Linear_Transformation)__

element types are described here
__[http://opensees.berkeley.edu/wiki/index.php/Element_Command](http://opensees.berkeley.edu/wiki/index.php/Element_Command)__



In [38]:
def BuildOpenSEES(MODEL):
    """"
    Function to generate model in Opensees

    """
    NODES = MODEL['NODES']
    SHELLS = MODEL['SHELLS']
    BEAMS = MODEL['BEAMS']
    LINKS = MODEL['LINKS']
    BCS = MODEL['BCS']
    LOAD = MODEL['LOAD']
    Mesh_X = MODEL['Mesh_X']
    Mesh_Y = MODEL['Mesh_Y']
    Deck_inp = MODEL['Deck_inp']
    Girders_inp = MODEL['Girders_inp']
    Diaphragms_inp = MODEL['Diaphragms_inp']
    Sections_inp = MODEL['Sections_inp']
    DeckSections_inp = MODEL['DeckSections_inp']
    BC_inp = MODEL['BC_inp']
    Materials_inp = MODEL['Materials_inp']

    # remove existing model
    opensees.wipe()

    # set modelbuilder, basic 3d model
    opensees.model('basic', '-ndm', 3)
    # ---------------------------------------------------------------------------------------
    # create nodes

    for n in sorted(NODES.keys()):
        opensees.node(int(n), *[float(NODES[n]['x']), float(NODES[n]['y']), float(NODES[n]['z'])])

    # ---------------------------------------------------------------------------------------
    # boundary conditions

    for n in sorted(BCS.keys()):
        opensees.fix(int(n), *BCS[n])

    # ---------------------------------------------------------------------------------------
    # define materials

    # for m in MATERIALS:
    #    opensees.nDMaterial('ElasticIsotropic', int(m), float(MATERIALS[m]['E']),
    #                        float(MATERIALS[m]['Nu']), float(MATERIALS[m]['Rho']))

    # ---------------------------------------------------------------------------------------
    # define beam elements

    # transfArgs=[$vecxzX,$vecxzY,$vecxzZ]
    transfTag_G = 1
    transfArgs_G = [0.0, -1.0, 0.0]
    opensees.geomTransf("Linear", int(transfTag_G), *transfArgs_G)
    transfTag_D = 2
    transfArgs_D = [1.0, 0.0, 0.0]
    opensees.geomTransf("Linear", int(transfTag_D), *transfArgs_D)

    for b in BEAMS:
        prop = BEAMS[b][2]
        mat = Sections_inp[prop]['mat']
        if prop == 1:
            transfTag = transfTag_D
        else:
            transfTag = transfTag_G
        
        opensees.element('elasticBeamColumn', int(b), *[BEAMS[b][0],BEAMS[b][1]],
                         Sections_inp[prop]['A'],Materials_inp[mat]['E'], Materials_inp[mat]['G'],  
                         Sections_inp[prop]['J'], Sections_inp[prop]['Iy'],Sections_inp[prop]['Ix'],
                         transfTag,'-mass',float(Sections_inp[prop]['A']*Materials_inp[mat]['Rho']),'-cmass')
        '''
        opensees.element('ElasticTimoshenkoBeam', int(b), *[BEAMS[b][0], BEAMS[b][1]],
                         Materials_inp[mat]['E'], Materials_inp[mat]['G'], Sections_inp[prop]['A'],
                         Sections_inp[prop]['J'], Sections_inp[prop]['Iy'], Sections_inp[prop]['Ix'], Sections_inp[prop]['Ay'],
                         Sections_inp[prop]['Ax'], transfTag, '-mass', float(Sections_inp[prop]['A']*Materials_inp[mat]['Rho']), "-cMass")
        '''
    # ---------------------------------------------------------------------------------------
    # define shell sections
    for d in sorted(DeckSections_inp.keys()):
        prop = d
        mat = DeckSections_inp[prop]['mat']
        nsm = DeckSections_inp[prop]['nsm']
        thick = DeckSections_inp[prop]['thick']

        '''
        opensees.section('ElasticMembranePlateSection', int(d), float(Materials_inp[mat]['E']),
                         float(Materials_inp[mat]['Nu']+nsm/thick),
                         float(thick), float(Materials_inp[mat]['Rho']))
        '''
        
        E = float(Materials_inp[mat]['E'])
        Nu = float(Materials_inp[mat]['Nu']+nsm/thick)
        rho = float(Materials_inp[mat]['Rho'])
    
        #if shear modulus is zero, use orthotropic material with small non-zero G. 
        if Materials_inp[mat]['G']==0:        
            Materials_inp[mat]['G']
            G = float(Materials_inp[m]['E']) / (2.0*(1.0+Materials_inp[mat]['Nu']))
            Gzero = G/10.0e6
            opensees.nDMaterial('ElasticOrthotropic', int(d), E, E, E, 0, Nu, Nu, Gzero, G, G, rho)
        else:
            opensees.nDMaterial('ElasticIsotropic', int(d), E, Nu, rho)
        
        opensees.section('PlateFiber', int(d), int(d), float(thick))
        

    # define shell elements as ShellMITC4 elements  (do these have membrane action, or just bending?)
    for s in sorted(SHELLS.keys()):
        # ShellMITC4
        #opensees.element('ShellMITC4', int(s), *SHELLS[s]['nodes'], int(SHELLS[s]['prop']))
        # ShellDKGQ
        opensees.element('ShellDKGQ',int(s),*SHELLS[s]['nodes'],int(SHELLS[s]['prop']))

    # ---------------------------------------------------------------------------------------
    # define links
    for l in sorted(LINKS.keys()):
        if LINKS[l][2]=='Composite':
            opensees.rigidLink('beam', LINKS[l][0], LINKS[l][1])
        elif LINKS[l][2]=='Noncomposite':
            #opensees.rigidLink('beam', LINKS[l][0], LINKS[l][1])
            #for non-composite link, connect longitudinal (1), transverse (2) and vertical (3) translations
            # and rotations about transverse (5) and vertical (6)
            opensees.equalDOF(LINKS[l][0], LINKS[l][1], *[2,3,4,6])

    # ---------------------------------------------------------------------------------------
    # define loads
    # create TimeSeries
    opensees.timeSeries("Constant", 1)

    # create a plain load pattern
    opensees.pattern("Plain", 1, 1)

    # unit point load at node 1001045 in -z direction
    for ptload in LOAD:
        opensees.load(int(ptload[0]), *[0.0, 0.0, float(ptload[1]), 0.0, 0.0, 0.0])

    return None

# RunOpenSEES

This function defines the run options, most of them are hard coded. The system option is available as optional user input. 
__[http://opensees.berkeley.edu/wiki/index.php/System_Command](http://opensees.berkeley.edu/wiki/index.php/System_Command)__

In [39]:
def RunOpenSEES(MODEL, system="BandGeneral"):
    """"
    Function to run model in OpenSEES

    """
    BCS = MODEL['BCS']

    # create SOE
    opensees.system(system)

    # create DOF number
    opensees.numberer("RCM")

    # create constraint handler
    opensees.constraints("Transformation")

    # create integrator
    opensees.integrator("LoadControl", 1.0)

    # create algorithm
    opensees.algorithm("Linear")

    # create analysis object
    opensees.analysis("Static")

    # record reactions
    opensees.recorder('Node', '-file', 'nodes.txt', '-time', '-node',
                      *[sorted(BCS.keys())], '-dof', *[1, 2, 3, 4, 5, 6], 'reaction')

    # run the analysis
    res = opensees.analyze(1)

    return res

# PlotGirderResults

This function generates a 3d scatter plot of beam elements, with an overlay using the vertical axis to report a specified beam element output quantity. Output quanties are: Fx Fy Fz Mx My Mz  (needs a reference).

__[http://opensees.berkeley.edu/OpenSees/manuals/usermanual/259.htm](http://opensees.berkeley.edu/OpenSees/manuals/usermanual/259.htm)__

In [40]:
def PlotGirderResults(MODEL, RESULTS, dofname):
    """
    Function to plot results
    """
    NODES = MODEL['NODES']
    BEAMS = MODEL['BEAMS']
    res = RESULTS['BEAMFORCES']
    dof = ['FX', 'FY', 'FZ', 'MX', 'MY', 'MZ'].index(dofname)
    # FX FY FZ MX MY MZ
    Labels = {0: 'Axial Force (FX)', 1: 'Shear Force (FY)', 2: 'Shear Force (FZ)',
              3: "Torsion (MX)", 4: "Bending (MY)", 5: "Bending (MZ)"}
    DEFAULT_PLOTLY_COLORS = ['rgb(31, 119, 180)', 'rgb(255, 127, 14)',
                             'rgb(44, 160, 44)', 'rgb(214, 39, 40)',
                             'rgb(148, 103, 189)', 'rgb(140, 86, 75)',
                             'rgb(227, 119, 194)', 'rgb(127, 127, 127)',
                             'rgb(188, 189, 34)', 'rgb(23, 190, 207)']
    beam_trace = []
    for b in [b for b in sorted(BEAMS.keys()) if b < 5000000]:
        if b == sorted(BEAMS.keys())[0]:
            showlegend = True
        else:
            showlegend = False
        beam_trace.append(go.Scatter3d(x=[NODES[BEAMS[b][0]]['x'],
                                           NODES[BEAMS[b][1]]['x']],
                                       y=[NODES[BEAMS[b][0]]['y'],
                                           NODES[BEAMS[b][1]]['y']],
                                       z=[NODES[BEAMS[b][0]]['z'],
                                           NODES[BEAMS[b][1]]['z']],
                                       mode='lines', legendgroup='beams', showlegend=showlegend, text=b,
                                       name='Beams', line=dict(color='black')))
    dy = max([NODES[n]['y'] for n in NODES.keys()]) - min([NODES[n]['y'] for n in NODES.keys()])
    dr = max([res[b][dof] for b in res.keys()]) - min([res[b][dof] for b in res.keys()])
    sf = dy/dr
    res_trace = []

    cmax = None
    cmin = None
    for b in [b for b in sorted(BEAMS.keys()) if b < 5000000]:
        if cmax == None:
            cmax = max([res[b][dof], -res[b][dof+6]])
            cmin = min([res[b][dof], -res[b][dof+6]])
        else:
            cmax = max([cmax, res[b][dof], -res[b][dof+6]])
            cmin = min([cmin, res[b][dof], -res[b][dof+6]])

    for b in [b for b in sorted(BEAMS.keys()) if b < 5000000]:
        if b == sorted(BEAMS.keys())[0]:
            showlegend = True
        else:
            showlegend = False
        res_trace.append(go.Scatter3d(x=[NODES[BEAMS[b][0]]['x'], NODES[BEAMS[b][1]]['x']],
                                      y=[NODES[BEAMS[b][0]]['y'], NODES[BEAMS[b][1]]['y']],
                                      z=[NODES[BEAMS[b][0]]['z']+res[b][dof]*sf,
                                          NODES[BEAMS[b][1]]['z']+res[b][dof+6]*-sf],
                                      text=[res[b][dof], -res[b][dof+6]], mode='lines+markers',
                                      legendgroup='res', showlegend=showlegend, name='Results',
                                      # line=dict(color='black')
                                      line=dict(color=[res[b][dof], -res[b][dof+6]], colorscale='Viridis',
                                                cmin=cmin, cmax=cmax, width=6),
                                      marker=dict(showscale=True, colorbar=dict(tickfont=dict(size=20), x=0.00, xanchor='left', showticklabels=True),
                                                  size=0, symbol='circle', color=[res[b][dof], -res[b][dof+6]], colorscale='Viridis', cmin=cmin, cmax=cmax)))

    # layout
    noaxis = dict(showbackground=False, showline=False, zeroline=False,
                  showgrid=False, showticklabels=False, title='')
    layout = dict(title=Labels[dof], scene=dict(aspectmode='data', xaxis=noaxis, yaxis=noaxis, zaxis=noaxis))
    fig = go.Figure(data=beam_trace+res_trace, layout=layout)
    py.iplot(fig)
    return None

# Extract Results
Pull nodal displacements, beam forces and reaction forces.

In [41]:
def ExtractResults(MODEL):
    NODES = MODEL['NODES']
    BEAMS = MODEL['BEAMS']
    BCS = MODEL['BCS']

    # request reactions
    opensees.reactions()

    DISP = {}
    for n in sorted(NODES.keys()):
        D1 = opensees.nodeDisp(int(n))
        DISP[n] = {'x': D1[0], 'y': D1[1], 'z': D1[2]}

    BEAMFORCES = {}
    for b in sorted(BEAMS.keys()):
        #BEAMFORCES[b] = opensees.eleForce(int(b))
        BEAMFORCES[b] = opensees.eleResponse(int(b), 'forces')

    REACTIONS = {}
    for n in sorted(BCS.keys()):
        REACTIONS[n] = opensees.nodeReaction(n)

    # visualize reactions somehow
    REACT = {}
    for x in [0, 780]:
        REACT[x] = {'x': {}, 'y': {}, 'z': {}}
        REACT[x] = {'x': {}, 'y': {}, 'z': {}}
        REACT[x]['x'] = {NODES[n]['y']: round(
            REACTIONS[n][0], 1) for n in BCS.keys() if NODES[n]['x'] == x}
        REACT[x]['y'] = {NODES[n]['y']: round(
            REACTIONS[n][1], 1) for n in BCS.keys() if NODES[n]['x'] == x}
        REACT[x]['z'] = {NODES[n]['y']: round(
            REACTIONS[n][2], 1) for n in BCS.keys() if NODES[n]['x'] == x}

    print("Pinned End Reactions", "\n", "\tLongitudinal")
    pp.pprint(REACT[0]['x'])
    print("\tTransverse")
    pp.pprint(REACT[0]['y'])
    print("\tVertical")
    pp.pprint(REACT[0]['z'])

    print("\n\nExpansion End Reactions", "\n", "\tLongitudinal")
    pp.pprint(REACT[780]['x'])
    print("\tTransverse")
    pp.pprint(REACT[780]['y'])
    print("\tVertical")
    pp.pprint(REACT[780]['z'])
    RESULTS = {'DISP': DISP, 'BEAMFORCES': BEAMFORCES, 'REACTIONS': REACTIONS}
    return RESULTS

<a id='inputcell'></a>
# User Inputs

The user's inputs must be in consistent units. (in and lbf is used in this example)
 - Mesh_X: the maximum shell element dimension in the longitudinal direction
 - Mesh_Y: the maximum shell element dimension in the transverse direction
 - Deck_inp: a dictionary defining the deck regions by coordinates and property number
 - DeckSection_inp: a dictionary defining deck section properties
 - Girders_inp: a dictionary defining each girder line, inputs are the X,prop,X,prop,X.... as many as needed to define the full girder line, followed by Z coordinate. (need to revise to allow different properties at different elevations)
 - BC_inp: boundary condtion inputs by coordinate, these x & y coordinates need to correspond to the other geometry inputs. Dof inputs are TX, TY, TZ, RX, RY, RZ. 1 is restrained, 0 is free.
 - Sections_inp: a dictionary defining beam cross section parameters. (Should be revised to use y and z since per __[http://opensees.berkeley.edu/wiki/index.php/Linear_Transformation](http://opensees.berkeley.edu/wiki/index.php/Linear_Transformation)__ )
 - Materials_inp: a dictionary defining material properties. 

In [42]:
# -----------------------------
# Inputs
# consistent units: in,lb
# -----------------------------

# Mesh
Mesh_X = 10
Mesh_Y = 10

# Deck
Deck_inp = {}
# Deck_inp[No]=[(Xstart,Xend),(Ystart,Yend),prop]
Deck_inp[1] = [(0, 780), (-143, 143), 1]

# DECK PROPERTIES
DeckSections_inp = {}
DeckSections_inp[1] = {"thick": 7.25, "nsm": 0, "mat": 2}

# Girders
Girders_inp = {}
# Girders_inp[Y]=[X,prop,X,prop,X,prop,X,Z]
Girders_inp[-132.0] = [0., 2, 150., 3, 630., 2, 780., -24.]
Girders_inp[-44.0] = [0., 2, 162., 4, 618., 2, 780., -24.]
Girders_inp[44.0] = [0., 2, 162., 4, 618., 2, 780., -24.]
Girders_inp[132.0] = [0., 2, 150., 3, 630., 2, 780., -24.]

# Boundary Conditions
BC_inp = {}
# BC_inp[(x,y,z)]=[dof1,dof2,dof3,dof4,dof5,dof6] (1 for restrained, 0 for free)
BC_inp[(0., -132., -44.375)] = [1, 1, 1, 0, 0, 0]
BC_inp[(0., -44., -44.375)] = [1, 1, 1, 0, 0, 0]
BC_inp[(0., 44., -44.375)] = [1, 1, 1, 0, 0, 0]
BC_inp[(0., 132., -44.375)] = [1, 1, 1, 0, 0, 0]
BC_inp[(780., -132., -44.375)] = [0, 1, 1, 0, 0, 0]
BC_inp[(780., -44., -44.375)] = [0, 1, 1, 0, 0, 0]
BC_inp[(780., 44., -44.375)] = [0, 1, 1, 0, 0, 0]
BC_inp[(780., 132., -44.375)] = [0, 1, 1, 0, 0, 0]

# Diaphragms
Diaphragms_inp = {}
# Diaphragms_inp[X]=prop
Diaphragms_inp[0.0] = 1
Diaphragms_inp[195.0] = 1
Diaphragms_inp[390.0] = 1
Diaphragms_inp[585.0] = 1
Diaphragms_inp[780.0] = 1

# BEAM SECTIONS
'''
Sections_inp = {}
#Sections_inp[i] = {"A","Ix","Iy","J","Ax","Ay"}
Sections_inp[1] = {"A": 12.475,  "Ix": 549.035, "Iy": 15.6833,
                   "J": 1.10832, "Ax": 1.66727, "Ay": 7.40825, "mat": 1}
Sections_inp[2] = {"A": 37.8712, "Ix": 6607.75, "Iy": 217.235,
                   "J": 6.73246, "Ax": 16.6574, "Ay": 18.2646, "mat": 1}
Sections_inp[3] = {"A": 45.6822, "Ix": 8414.14, "Iy": 288.743,
                   "J": 18.3722, "Ax": 23.2446, "Ay": 18.6911, "mat": 1}
Sections_inp[4] = {"A": 44.5148, "Ix": 8277.46, "Iy": 276.798,
                   "J": 15.5185, "Ax": 22.126, "Ay": 18.7483, "mat": 1}
# stiff beam
Sections_inp[5] = {"A": 44.5148, "Ix": 8277.46, "Iy": 276.798,
                   "J": 15.5185, "Ax": 22.126, "Ay": 18.7483, "mat": 3}
'''
Sections_inp = {}
#Sections_inp[i] = {"A","Ix","Iy","J","Ax","Ay"}
Sections_inp[1] = {"A": 12.475,  "Ix": 549.035, "Iy": 15.6833,
                   "J": 1.10832, "Ax": 0, "Ay": 0, "mat": 1}
Sections_inp[2] = {"A": 37.8712, "Ix": 6607.75, "Iy": 217.235,
                   "J": 6.73246, "Ax": 0, "Ay": 0, "mat": 1}
Sections_inp[3] = {"A": 45.6822, "Ix": 8414.14, "Iy": 288.743,
                   "J": 18.3722, "Ax": 0, "Ay": 0, "mat": 1}
Sections_inp[4] = {"A": 44.5148, "Ix": 8277.46, "Iy": 276.798,
                   "J": 15.5185, "Ax": 0, "Ay": 0, "mat": 1}
# stiff beam
Sections_inp[5] = {"A": 44.5148, "Ix": 8277.46, "Iy": 276.798,
                   "J": 15.5185, "Ax": 0, "Ay": 0, "mat": 3}


# MATERIALS
Materials_inp = {}
# MATERIALS
# steel
Materials_inp[1] = {"E": 29000000.0, "Nu": 0.29, "Rho": 490/12.**3}
# conc
Materials_inp[2] = {"E": 3122000.0, "Nu": 0.2, "Rho": 150/12.**3}
Materials_inp[3] = {"E": 29000000000000.0, "Nu": 0.29, "Rho": 490/12.**3}
for m in Materials_inp:
    if 'G' not in Materials_inp[m]:
        Materials_inp[m]['G'] = Materials_inp[m]['E'] / (2*(1+Materials_inp[m]['Nu']))

Comp_inp = 'Composite'

## Generate then plot the model

(may need to hover mouse over the plot for it to appear)

In [43]:
Model0_Inp = {'Mesh_X': Mesh_X, 'Mesh_Y': Mesh_Y, 'Deck_inp': Deck_inp, 'Girders_inp': Girders_inp,
              'Diaphragms_inp': Diaphragms_inp, 'BC_inp': BC_inp,'Comp_inp':Comp_inp,
              'DeckSections_inp':DeckSections_inp,'Sections_inp':Sections_inp,'Materials_inp':Materials_inp,
              'Name':"Model0"}
MODEL0,gridx0,gridy0 = GenerateModel(Model0_Inp)
print('Mesh is '+"%i"%len(gridx0)+' by '+"%i"%len(gridy0)+' nodes')
print('Nodes=', len(MODEL0['NODES']))
print('Shells=', len(MODEL0['SHELLS']))
print('Beams=', len(MODEL0['BEAMS']))
print('Links=', len(MODEL0['LINKS']))
print('BCs=', len(MODEL0['BCS']))

Mesh is 83 by 32 nodes
Nodes= 2996
Shells= 2542
Beams= 351
Links= 332
BCs= 8


In [ ]:
PlotModel(MODEL0)

### Chose node to load then build and run OpenSEES model

In [ ]:
gridx0

#LOAD0 = [(1003045, -1000.)]
#LOAD0 = [deck, edge, midspan]
LOAD0 = [(1e6 + 1e3 + int(len(gridx0)/2), -1000.)]
MODEL0['LOAD'] = LOAD0
print(MODEL0.keys())
BuildOpenSEES(MODEL0)

dict_keys(['NODES', 'SHELLS', 'BEAMS', 'LINKS', 'BCS', 'Mesh_X', 'Mesh_Y', 'Deck_inp', 'Girders_inp', 'Diaphragms_inp', 'BC_inp', 'Comp_inp', 'DeckSections_inp', 'Sections_inp', 'Materials_inp', 'Name', 'LOAD'])


In [ ]:
# perform the analysis
RunOpenSEES(MODEL0)

# print model to file
# opensees.printModel('-file','Model1.json')

0

### Extract results

In [ ]:
RESULTS0 = ExtractResults(MODEL0)

Pinned End Reactions 
 	Longitudinal
{-132.0: 1596.5, -44.0: 318.5, 44.0: -606.1, 132.0: -1308.9}
	Transverse
{-132.0: 92.2, -44.0: 182.2, 44.0: 175.3, 132.0: 94.1}
	Vertical
{-132.0: 583.4, -44.0: 204.0, 44.0: -9.5, 132.0: -265.5}


Expansion End Reactions 
 	Longitudinal
{-132.0: 0.0, -44.0: 0.0, 44.0: 0.0, 132.0: -0.0}
	Transverse
{-132.0: -105.1, -44.0: -166.5, 44.0: -172.6, 132.0: -99.6}
	Vertical
{-132.0: 186.0, -44.0: 173.0, 44.0: 72.3, 132.0: 56.3}


### Plot Results

(may need to hover mouse over the plot for it to appear)

In [ ]:
PlotModel(MODEL0, True, RESULTS0, 10000, 'z')

In [ ]:
# plot axial forces
PlotGirderResults(MODEL0, RESULTS0, 'FX')

## Model Changes
The Model_0 generated above is considered the __baseline__ model. It has 5 characteristics required to produce pinned end moments in an finite element analysis. Below, five additional models are created each changing one parameter of the baseline model to demonstrate that the pinned end moment effect requires 


Model: Description 

    0: Baseline model showing pinned end moments 
    1: Make girders non-composite  (No pinned end moments) 
    2: Locate BC at girder centroid (No pinned end moments) 
    3: Only 1 longitudinal BC instead of every girder (No pinned end moments) 
    4: Remove transverse BC on roller bearing line (No pinned end moments) 
    5: Apply symmetric point loads (No pinned end Moments) 
    6: Remove shear modulus (no pinned end moments)

In [ ]:
#start by making a copy of the baseline model, then make edits

#Model0_Inp = {'Mesh_X': Mesh_X, 'Mesh_Y': Mesh_Y, 'Deck_inp': Deck_inp, 'Girders_inp': Girders_inp,
#              'Diaphragms_inp': Diaphragms_inp, 'BC_inp': BC_inp,'Comp_inp':Comp_inp}

Model1_Inp = copy.deepcopy(Model0_Inp)
Model2_Inp = copy.deepcopy(Model0_Inp)
Model3_Inp = copy.deepcopy(Model0_Inp)
Model4_Inp = copy.deepcopy(Model0_Inp)
Model5_Inp = copy.deepcopy(Model0_Inp)
Model6_Inp = copy.deepcopy(Model0_Inp)

#1: Non-composite
Model1_Inp['Comp_inp']="Noncomposite"
Model1_Inp['Name']="Model1"
MODEL1,_,_ = GenerateModel(Model1_Inp)
MODEL1['LOAD'] = LOAD0

#2: BC at centroid
BC_inp2 = {}

# find centroid, assume entire deck is active. Rather than finding centroid 
# for each girder and its effective deck width, use the entire deck width 
# and all girders.
Ea=0.
EaZ=0.
for g in Model2_Inp['Girders_inp']:
    Z = Model2_Inp['Girders_inp'][g][-1]
    prop = Model2_Inp['Girders_inp'][g][1]
    area = Model2_Inp['Sections_inp'][prop]['A']
    mat = Model2_Inp['Sections_inp'][prop]['mat']
    E = Materials_inp[mat]['E']
    Ea += E*area
    EaZ += E*area*Z
for d in Model2_Inp['Deck_inp']:
    Z = 0
    prop = Model2_Inp['Deck_inp'][d][2]
    mat = Model2_Inp['DeckSections_inp'][prop]['mat']
    thick = Model2_Inp['DeckSections_inp'][prop]['thick']
    E = Materials_inp[mat]['E']
    area = thick*(max(Model2_Inp['Deck_inp'][d][1]) - min(Model2_Inp['Deck_inp'][d][1]))
    Ea += E*area
    EaZ += E*area*Z

Zcg = EaZ/Ea

for coord in Model2_Inp['BC_inp']:
    #add the new
    newcoord = (coord[0],coord[1],Zcg)
    BC_inp2[newcoord] = Model2_Inp['BC_inp'][coord]
    #remove the old
Model2_Inp['BC_inp']=BC_inp2
Model2_Inp['Name']="Model2"
MODEL2,_,_ = GenerateModel(Model2_Inp)
MODEL2['LOAD'] = LOAD0


#3: 1 long BC
first=True
BC_inp3 = {}
for coord in Model3_Inp['BC_inp']:
    if coord[0]==0 and first:
        BC_inp3[coord] = Model3_Inp['BC_inp'][coord]
        first = False
    elif coord[0]==0 and not first:
        #change from restrained to free
        BC_inp3[coord] = Model3_Inp['BC_inp'][coord]
        BC_inp3[coord][0] = 0
    else:
        BC_inp3[coord] = Model3_Inp['BC_inp'][coord]
Model3_Inp['BC_inp']=BC_inp3
Model3_Inp['Name']="Model3"
MODEL3,_,_ = GenerateModel(Model3_Inp)
MODEL3['LOAD'] = LOAD0
        
#4: No transverse BC on roller bearing
BC_inp4 = {}
for coord in Model4_Inp['BC_inp']:
    if coord[0]!=0:
        #change from restrained to free
        BC_inp4[coord] = Model4_Inp['BC_inp'][coord]
        BC_inp4[coord][1]=0
    else:
        BC_inp4[coord] = Model4_Inp['BC_inp'][coord]
Model4_Inp['BC_inp']=BC_inp4
Model4_Inp['Name']="Model4"
MODEL4,_,_ = GenerateModel(Model4_Inp)
MODEL4['LOAD'] = LOAD0


#5: Symmetric loading
#load each girder
LOAD5=[]
for ycoord in Model3_Inp['Girders_inp']:
    node = 1e6 + 1e3*(gridy0.index(ycoord)+1)+int(len(gridx0)/2)
    LOAD5.append((node,-250.))
#LOAD5 = [(1e6 + 1e3 + len(gridx0)/2, -1000.),(1e6 + 1e3*len(gridy0) + len(gridx0)/2, -1000.)]
Model5_Inp['Name']="Model5"
MODEL5,_,_ = GenerateModel(Model5_Inp)
MODEL5['LOAD'] = LOAD5
print(LOAD0)
print(LOAD5)

#6: No deck shear stiffness
deckmats=[]
for ds in Model6_Inp['DeckSections_inp'].keys():
    mat = Model6_Inp['DeckSections_inp'][ds]['mat']
    if mat not in deckmats:
        deckmats.append(mat)
for mat in deckmats:
    Model6_Inp['Material_Inp'][mat]['G']=0


Only one model is generated & run at a time. Build an object to store results

In [ ]:
for m in [Model0_Inp,Model1_Inp,Model2_Inp,Model3_Inp,Model4_Inp,Model5_Inp,Model6_Inp]:
    print(m['Name'])
    pp.pprint(m)
    print("\n\n")

In [ ]:
ParamMODELS={'MODEL1':MODEL1, 'MODEL2':MODEL2, 'MODEL3':MODEL3, 'MODEL4':MODEL4, 'MODEL5':MODEL5, 'MODEL6':MODEL6}
ParamRESULTS={}

for i in sorted(ParamMODELS.keys()):
    print("Running ",i)

    BuildOpenSEES(ParamMODELS[i])
    # perform the analysis
    RunOpenSEES(ParamMODELS[i])

    # print model to file
    opensees.printModel('-file',ParamMODELS[i]['Name']+'.json')

    # Exract Results
    ParamRESULTS[i] = ExtractResults(ParamMODELS[i])

### Plot Results

In [ ]:
# explore ParamRESULTS (look at reactions)
PlotModel(MODEL6, True, ParamRESULTS['MODEL6'], 5000, 'z')

In [ ]:
# PlotModel(MODEL2,RESULTS2,10000,'ALL')
# PlotModel(MODEL2, True, RESULTS2, 10000, 'z')

In [ ]:
# plot axial forces
PlotGirderResults(MODEL6, ParamRESULTS['MODEL6`'], 'FX')

In [ ]:
# plot shear forces
# PlotGirderResults(MODEL1,RESULTS1,'FZ')
# PlotGirderResults(MODEL2,RESULTS2,'FZ')

In [ ]:
# plot bending moment
# PlotGirderResults(MODEL1,RESULTS1,'MY')
# PlotGirderResults(MODEL2,RESULTS2,'MY')

In [ ]:
#pp.pprint(RESULTS1['REACTIONS'])
#pp.pprint(RESULTS2['REACTIONS'])

In [ ]:
# create an HTML link to download your generated geometries
import base64
import pandas as pd
from IPython.display import HTML
def create_download_link(nodes ,filename = "data.csv"):  
    csv = nodes.to_csv()
    b64 = base64.b64encode(csv.encode())
    payload = b64.decode()
    #print(str(payload))
    html = '<a download="{filename}" href="data:text/csv;base64,{payload}" target="_blank">{title}</a>'
    html = html.format(payload=payload,title=filename,filename=filename)
    return HTML(html)

In [ ]:
#df_res0 = pd.DataFrame.from_dict(RESULTS0['BEAMFORCES'],'index')
#df_con0 = pd.DataFrame.from_dict(MODEL0['BEAMS'],'index')
#df_node0 = pd.DataFrame.from_dict(MODEL0['NODES'],'index')
#df_react0 = pd.DataFrame.from_dict(RESULTS0['REACTIONS'],'index')


In [ ]:
#create_download_link(df_react1 ,filename = "df_react1.csv")


In [ ]:
#create_download_link(df_res1 ,filename = "df_res1.csv")

In [ ]:
#create_download_link(df_react2 ,filename = "df_react2.csv")

In [ ]:
#create_download_link(df_res2 ,filename = "df_res2.csv")